# Principal Page

## Installs

In [2]:
!pip install streamlit

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.3/44.3 kB 1.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 9.1/9.1 MB 52.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 6.9/6.9 MB 93.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.1/79.1 kB 8.7 MB/s eta 0:00:00


In [3]:
!pip install streamlit_folium

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 328.5/328.5 kB 4.2 MB/s eta 0:00:00


## Imports

In [4]:
# Importação de bibliotecas
import pandas as pd
import numpy as np
import plotly.express as px
import streamlit as st
from PIL import Image
import folium
from folium.plugins import MarkerCluster
from streamlit_folium import folium_static
import re

2025-01-04 00:05:59.568 WARNING streamlit.runtime.scriptrunner_utils.script_run_context: Thread 'MainThread': missing ScriptRunContext! This warning can be ignored when running in bare mode.


## Funções

In [5]:
def rename_columns(dataframe):
    # Renomeia colunas
    renamed_dataframe = dataframe.copy()

    # Funções de transformação para as colunas
    title = lambda x: x.title()
    snakecase = lambda x: re.sub(r'([a-z])([A-Z])', r'\1_\2', x).lower().replace(" ", "_")
    spaces = lambda x: x.replace(" ", "")

    cols_old = [title(str(x)) for x in renamed_dataframe.columns]
    cols_old = [spaces(x) for x in cols_old]
    cols_new = [snakecase(x) for x in cols_old]

    renamed_dataframe.columns = cols_new
    return renamed_dataframe

In [6]:
def unicos(dataframe, coluna):
    # Retorna valores únicos
    return dataframe[coluna].nunique()

In [7]:
def Country_Maps(df):
    df_aux7 = df.loc[:, ['restaurant_name', 'country_name', 'latitude', 'longitude']].groupby(['restaurant_name', 'country_name']).median().reset_index()

    map = folium.Map()
    for _, location_info in df_aux7.iterrows():
        folium.Marker(
            [location_info['latitude'], location_info['longitude']],
            popup=f"{location_info['restaurant_name']} - {location_info['country_name']}"
        ).add_to(map)

    return map




In [8]:
@st.cache_data
def convert_df_to_csv(dataframe):
    """Converte o DataFrame em CSV e retorna como bytes."""
    return dataframe.to_csv(index=False).encode('utf-8')

2025-01-04 00:05:59.659 WARNING streamlit.runtime.caching.cache_data_api: No runtime found, using MemoryCacheStorageManager


In [9]:
def restaurant_statistics_graphs(df, graph_type):
    # Criando a coluna 'Colors_name' que mapeia a cor
    df['colors_name'] = df['rating_color'].apply(lambda x: COLORS.get(x, 'Unknown'))

    # Criando a coluna 'Rating_description' com o significado do rating
    df['rating_description'] = df['colors_name'].apply(lambda x: RATING_MEANING.get(x, 'Desconhecido'))

    if graph_type == 'restaurants':
        # 1. Quantidade de Restaurantes por País
        restaurants_by_country = df.groupby('country_name')['restaurant_id'].nunique().reset_index()
        restaurants_by_country = restaurants_by_country.rename(columns={'restaurant_id': 'restaurant_count'})

        # Adicionar a cor do rating como uma coluna para o gráfico
        restaurants_by_country['rating_color'] = df.groupby('country_name')['rating_color'].first().values

        # Gráfico de Restaurantes por País
        fig_restaurants = px.bar(restaurants_by_country,
                                 x='country_name',
                                 y='restaurant_count',
                                 title='Quantidade de Restaurantes por País',
                                 labels={'country_name': 'País', 'restaurant_count': 'Quantidade de Restaurantes'},
                                 color='rating_color',
                                 color_discrete_map=COLORS)

        # Remover a legenda automática do Plotly
        fig_restaurants.update_layout(showlegend=False)

        # Adicionar uma legenda manual no canto superior direito
        fig_restaurants.update_layout(
            annotations=[
                dict(
                    x=1, y=1, xref="paper", yref="paper",
                    text="Legenda de Rating:", showarrow=False, font=dict(size=14, color="black"),
                    align="left", xanchor="right", yanchor="top"
                ),
                dict(
                    x=1, y=0.95, xref="paper", yref="paper",
                    text="darkgreen: Excelente (4.5 - 5.0)", showarrow=False, font=dict(size=12),
                    align="left", xanchor="right", yanchor="top"
                ),
                dict(
                    x=1, y=0.90, xref="paper", yref="paper",
                    text="green: Muito bom (4.0 - 4.5)", showarrow=False, font=dict(size=12),
                    align="left", xanchor="right", yanchor="top"
                ),
                dict(
                    x=1, y=0.85, xref="paper", yref="paper",
                    text="lightgreen: Bom (3.5 - 4.0)", showarrow=False, font=dict(size=12),
                    align="left", xanchor="right", yanchor="top"
                ),
                dict(
                    x=1, y=0.80, xref="paper", yref="paper",
                    text="orange: Médio (3.0 - 3.5)", showarrow=False, font=dict(size=12),
                    align="left", xanchor="right", yanchor="top"
                ),
                dict(
                    x=1, y=0.75, xref="paper", yref="paper",
                    text="red: Ruim (2.5 - 3.0)", showarrow=False, font=dict(size=12),
                    align="left", xanchor="right", yanchor="top"
                ),
                dict(
                    x=1, y=0.70, xref="paper", yref="paper",
                    text="darkred: Péssimo (1.5 - 2.5)", showarrow=False, font=dict(size=12),
                    align="left", xanchor="right", yanchor="top"
                )
            ]
        )

        return fig_restaurants

    elif graph_type == 'cities':
        # 2. Quantidade de Cidades Registradas por País
        cities_by_country = df.groupby('country_name')['city'].nunique().reset_index()
        cities_by_country = cities_by_country.rename(columns={'city': 'city_count'})

        # Adicionar a cor do rating como uma coluna para o gráfico
        cities_by_country['rating_color'] = df.groupby('country_name')['rating_color'].first().values

        # Gráfico de Cidades por País
        fig_cities = px.bar(cities_by_country,
                            x='country_name',
                            y='city_count',
                            title='Quantidade de Cidades Registradas por País',
                            labels={'country_name': 'País', 'city_count': 'Quantidade de Cidades'},
                            color='rating_color',
                            color_discrete_map=COLORS)

        # Remover a legenda automática do Plotly
        fig_cities.update_layout(showlegend=False)

        # Adicionar uma legenda manual no canto superior direito
        fig_cities.update_layout(
            annotations=[
                dict(
                    x=1, y=1, xref="paper", yref="paper",
                    text="Legenda de Rating:", showarrow=False, font=dict(size=14, color="black"),
                    align="left", xanchor="right", yanchor="top"
                ),
                dict(
                    x=1, y=0.95, xref="paper", yref="paper",
                    text="darkgreen: Excelente (4.5 - 5.0)", showarrow=False, font=dict(size=12),
                    align="left", xanchor="right", yanchor="top"
                ),
                dict(
                    x=1, y=0.90, xref="paper", yref="paper",
                    text="green: Muito bom (4.0 - 4.5)", showarrow=False, font=dict(size=12),
                    align="left", xanchor="right", yanchor="top"
                ),
                dict(
                    x=1, y=0.85, xref="paper", yref="paper",
                    text="lightgreen: Bom (3.5 - 4.0)", showarrow=False, font=dict(size=12),
                    align="left", xanchor="right", yanchor="top"
                ),
                dict(
                    x=1, y=0.80, xref="paper", yref="paper",
                    text="orange: Médio (3.0 - 3.5)", showarrow=False, font=dict(size=12),
                    align="left", xanchor="right", yanchor="top"
                ),
                dict(
                    x=1, y=0.75, xref="paper", yref="paper",
                    text="red: Ruim (2.5 - 3.0)", showarrow=False, font=dict(size=12),
                    align="left", xanchor="right", yanchor="top"
                ),
                dict(
                    x=1, y=0.70, xref="paper", yref="paper",
                    text="darkred: Péssimo (1.5 - 2.5)", showarrow=False, font=dict(size=12),
                    align="left", xanchor="right", yanchor="top"
                )
            ]
        )

        return fig_cities

    else:
        print("Tipo de gráfico inválido. Use 'restaurants' ou 'cities'.")

In [10]:
def calculate_country_statistics(df, metric):
    """
    Calcula estatísticas por país com base na métrica escolhida.

    Parâmetros:
        df (pd.DataFrame): O DataFrame com os dados.
        metric (str): A métrica para calcular ("rating" ou "price").

    Retorna:
        pd.DataFrame: Resultado da média por país.
    """
    if metric == 'rating':
        # Média de avaliações por país
        result = df.groupby('country_name')['aggregate_rating'].mean().reset_index(name='average_rating')
        result = result.sort_values(by='average_rating', ascending=False).reset_index(drop=True)  # Ordenando e resetando índices
        return result

    elif metric == 'price':
        # Média de preço para duas pessoas por país
        result = df.groupby('country_name')['average_cost_for_two'].mean().reset_index(name='average_cost_for_two_people')
        result = result.sort_values(by='average_cost_for_two_people', ascending=False).reset_index(drop=True)  # Ordenando e resetando índices
        return result

    else:
        raise ValueError("Métrica inválida. Use 'rating' ou 'price'.")

In [11]:
def top_cities_analysis(df, analysis_type):
    """
    Encontra o Top 10 cidades com base no tipo de análise escolhida
    (mais restaurantes ou mais tipos culinários distintos) e gera um gráfico.

    Parâmetros:
        df (pd.DataFrame): O DataFrame com os dados.
        analysis_type (str): Tipo de análise ("restaurants" ou "cuisines").

    Retorna:
        None: Exibe o gráfico no Streamlit.
    """
    if analysis_type == 'restaurants':
        # Contar o número de restaurantes por cidade
        result = (
            df.groupby('city')['restaurant_id']
            .count()
            .reset_index(name='restaurant_count')
            .sort_values(by='restaurant_count', ascending=False)
            .head(10)
        )
        title = "Top 10 Cidades com Mais Restaurantes"
        y_axis = "restaurant_count"

    elif analysis_type == 'cuisines':
        # Contar o número de tipos culinários distintos por cidade
        result = (
            df.groupby('city')['cuisines']
            .nunique()
            .reset_index(name='distinct_cuisines_count')
            .sort_values(by='distinct_cuisines_count', ascending=False)
            .head(10)
        )
        title = "Top 10 Cidades com Mais Tipos Culinários Distintos"
        y_axis = "distinct_cuisines_count"

    else:
        raise ValueError("Tipo de análise inválido. Use 'restaurants' ou 'cuisines'.")

    # Criar o gráfico com Plotly Express
    fig = px.bar(
        result,
        x='city',
        y=y_axis,
        text=y_axis,
        title=title,
        labels={'city': 'Cidades', y_axis: 'Quantidade'},
        template='plotly_white',
    )
    fig.update_traces(textposition='outside')
    fig.update_layout(
        xaxis_title='Cidades',
        yaxis_title='Quantidade',
        showlegend=False
    )

    # Exibir o gráfico
    return fig

In [12]:
def cities_with_rating_range(df, min_rating, max_rating):
    """
    Cria um gráfico das 5 principais cidades com média de avaliações dentro de um intervalo definido pelo usuário.

    Parâmetros:
        df (pd.DataFrame): O DataFrame com os dados.
        min_rating (float): Avaliação mínima.
        max_rating (float): Avaliação máxima.

    Retorna:
        None: Exibe o gráfico no Streamlit.
    """
    # Agrupar os dados por cidade e calcular a média de avaliação
    filtered_df = (
        df.groupby('city')['aggregate_rating']
        .mean()
        .reset_index(name='average_rating')
    )

    # Filtrar pelo intervalo definido pelo usuário
    filtered_df = filtered_df[
        (filtered_df['average_rating'] >= min_rating) &
        (filtered_df['average_rating'] <= max_rating)
    ].sort_values(by='average_rating', ascending=False).head(5)

    if filtered_df.empty:
        st.warning("Nenhuma cidade encontrada no intervalo especificado.")
        return

    # Criar o gráfico com Plotly Express
    fig = px.bar(
        filtered_df,
        x='city',
        y='average_rating',
        text='average_rating',
        title=f'Top 5 Cidades com Média de Avaliações entre {min_rating} e {max_rating}',
        labels={'city': 'Cidades', 'average_rating': 'Média de Avaliação'},
        template='plotly_white',
    )
    fig.update_traces(textposition='outside')
    fig.update_layout(
        xaxis_title='Cidades',
        yaxis_title='Média de Avaliação',
        showlegend=False,
        title_x=0.5,
    )

    # Exibir o gráfico
    return fig

In [30]:
def best_restaurants_by_cuisine(df, top_n_cuisines=5):
    """
    Encontra os melhores restaurantes com base na avaliação agregada
    para os tipos culinários mais populares.

    Parâmetros:
        df (pd.DataFrame): O DataFrame com os dados.
        top_n_cuisines (int): O número de tipos culinários mais populares a considerar.

    Retorna:
        pd.DataFrame: DataFrame com os melhores restaurantes por tipo culinário.
    """
    # Contar a quantidade de restaurantes por tipo culinário
    cuisine_counts = (
        df['cuisines']
        .value_counts()
        .head(top_n_cuisines)
        .index
    )

    # Filtrar apenas os tipos culinários mais populares
    popular_cuisines_df = df[df['cuisines'].isin(cuisine_counts)]

    # Encontrar os melhores restaurantes (maior avaliação) por tipo culinário
    best_restaurants = (
        popular_cuisines_df.loc[popular_cuisines_df.groupby('cuisines')['aggregate_rating'].idxmax()]
    )

    # Selecionar colunas relevantes
    result = best_restaurants[
        ['restaurant_name', 'cuisines', 'aggregate_rating', 'city', 'country_name']
    ].sort_values(by='aggregate_rating', ascending=False)

    return result

In [35]:
def top_10_restaurants(df):
    """
    Função para encontrar os top 10 restaurantes com maior média de avaliação (aggregate_rating).

    Parâmetros:
        df (pd.DataFrame): O DataFrame com os dados de restaurantes.

    Retorna:
        pd.DataFrame: DataFrame com os top 10 restaurantes por avaliação.
    """
    # Ordenar o DataFrame pela coluna 'aggregate_rating' em ordem decrescente
    top_10_df = df.sort_values(by='aggregate_rating', ascending=False).head(10)

    # Selecionando colunas relevantes para exibir
    top_10_df = top_10_df[['restaurant_name', 'country_name', 'city', 'aggregate_rating']]

    return top_10_df

In [38]:
def top_10_cuisines_by_rating(df, top_or_bottom='top'):
    """
    Calcula os 10 melhores ou 10 piores tipos culinários com base na média de avaliação (aggregate_rating)
    e gera um gráfico de barras usando Plotly Express.

    Parâmetros:
        df (pd.DataFrame): O DataFrame com os dados de restaurantes.
        top_or_bottom (str): Se 'top', retorna os 10 melhores tipos culinários. Se 'bottom', retorna os 10 piores.

    Retorna:
        fig: Gráfico de barras Plotly.
    """
    # Agrupar por tipo de culinária e calcular a média de aggregate_rating
    cuisine_rating = df.groupby('cuisines')['aggregate_rating'].mean().reset_index()

    # Ordenar os valores com base na média de aggregate_rating
    if top_or_bottom == 'top':
        top_10 = cuisine_rating.sort_values(by='aggregate_rating', ascending=False).head(10)
    elif top_or_bottom == 'bottom':
        top_10 = cuisine_rating.sort_values(by='aggregate_rating', ascending=True).head(10)
    else:
        raise ValueError("O parâmetro 'top_or_bottom' deve ser 'top' ou 'bottom'")

    # Criar o gráfico de barras com Plotly Express
    fig = px.bar(
        top_10,
        x='cuisines',
        y='aggregate_rating',
        title=f'Top 10 Tipos Culinários - { "Melhores" if top_or_bottom == "top" else "Piores" } Avaliações',
        labels={'cuisines': 'Tipo de Culinária', 'aggregate_rating': 'Média de Avaliação'},
        color='aggregate_rating',
        color_continuous_scale='Viridis'
    )

    # Exibir o gráfico
    return fig

# Importando dados

In [13]:
df = pd.read_csv("zomato.csv")
df1 = df.dropna()

# Configurações iniciais

In [14]:
COUNTRIES = {
    1: "India",
    14: "Australia",
    30: "Brazil",
    37: "Canada",
    94: "Indonesia",
    148: "New Zealand",
    162: "Philippines",
    166: "Qatar",
    184: "Singapore",
    189: "South Africa",
    191: "Sri Lanka",
    208: "Turkey",
    214: "United Arab Emirates",
    215: "England",
    216: "United States of America"
}
df1['country_name'] = df1['Country Code'].apply(lambda x: COUNTRIES.get(x, 'Unknown'))

COLORS = {
    "3F7E00": 'darkgreen',
    "5BA829": 'green',
    "9ACD32": 'lightgreen',
    "CDD614": 'orange',
    "FFBA00": 'red',
    "CBCBC8": 'darkred',
    "FF7800": 'darkred'
}
df1['Colors_name'] = df1['Rating color'].apply(lambda x: COLORS.get(x, 'Unknown'))

# Definindo as cores e seus significados de rating
RATING_MEANING = {
    "darkgreen": "Excelente (4.5 - 5.0)",
    "green": "Muito bom (4.0 - 4.5)",
    "lightgreen": "Bom (3.5 - 4.0)",
    "orange": "Médio (3.0 - 3.5)",
    "red": "Ruim (2.5 - 3.0)",
    "darkred": "Péssimo (1.5 - 2.5)",
    "Unknown": "Desconhecido"
}

# Criando a coluna 'Rating_description' baseada na 'Colors_name'
df1['Rating_description'] = df1['Colors_name'].apply(lambda x: RATING_MEANING.get(x, 'Desconhecido'))

df2 = rename_columns(df1)
df2['cuisines'] = df2.loc[:, "cuisines"].apply(lambda x: x.split(",")[0])
df3 = df2.drop('switch_to_order_menu', axis=1)
df4 = df3.drop_duplicates()

<ipython-input-14-3e32bb4eff18>:18: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1['country_name'] = df1['Country Code'].apply(lambda x: COUNTRIES.get(x, 'Unknown'))
<ipython-input-14-3e32bb4eff18>:29: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df1['Colors_name'] = df1['Rating color'].apply(lambda x: COLORS.get(x, 'Unknown'))
<ipython-input-14-3e32bb4eff18>:43: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value in

# Valores, Colunas e Tabelas

## Principal page

### Container 1 - Temos os seguintes marcos dentro de nossa plataforma

#### col1 - Restaurantes

In [15]:
unicos(df4, coluna="restaurant_id")

6929

#### col2 - Países

In [16]:
unicos(df4, coluna="country_code")

15

#### col3 - Cidades

In [17]:
 unicos(df4, coluna="city")

125

#### col4 - Avaliações

In [18]:
df4['votes'].sum()

4194533

#### col5 - Culinárias

In [19]:
unicos(df4, coluna="cuisines")

165

### Container 2 - Mapa restaurantes mundo

In [20]:
Country_Maps(df4)

## Country Views

### Container 1 - Quantidade de Restaurantes por País

In [21]:
restaurant_statistics_graphs(df4, graph_type='restaurants')

<ipython-input-9-712f94c97598>:3: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['colors_name'] = df['rating_color'].apply(lambda x: COLORS.get(x, 'Unknown'))
<ipython-input-9-712f94c97598>:6: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['rating_description'] = df['colors_name'].apply(lambda x: RATING_MEANING.get(x, 'Desconhecido'))


### Container 2 - Quantidade de Cidades Registradas por País

In [22]:
restaurant_statistics_graphs(df4, graph_type='cities')

<ipython-input-9-712f94c97598>:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

<ipython-input-9-712f94c97598>:6: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



### Container 3 - *Médias*

#### col1 - Média de avaliações feitas por país

In [23]:
calculate_country_statistics(df4,'rating')

country_name  average_rating
0                  Indonesia        4.601250
1                Philippines        4.463750
2                  Singapore        4.435000
3   United States of America        4.402693
4                  Australia        4.372778
5                     Canada        4.321667
6                     Turkey        4.310063
7                      Qatar        4.240000
8                New Zealand        4.164435
9               South Africa        4.061561
10                 Sri Lanka        4.057500
11                   England        4.041750
12                     India        4.037126
13      United Arab Emirates        4.023667
14                    Brazil        3.321667

#### col2 - Média de preço de um prato para duas pessoas por país

In [24]:
calculate_country_statistics(df4,'price')

country_name  average_cost_for_two_people
0                  Indonesia                303000.000000
1                  Australia                138959.783333
2                  Sri Lanka                  2579.375000
3                Philippines                  1227.825000
4                      India                   704.400514
5               South Africa                   339.228324
6                      Qatar                   174.000000
7       United Arab Emirates                   153.716667
8                  Singapore                   141.437500
9                     Brazil                   138.812500
10                    Turkey                   128.584906
11               New Zealand                    62.154812
12  United States of America                    55.029840
13                   England                    43.510000
14                    Canada                    41.861111

## City views

### Container 1 - Top 10 cidades com mais restaurantes na base de dados

In [25]:
top_cities_analysis(df4, 'restaurants')

### Container 2 - Média das cidades

#### col1 - Cidades com média de avaliações acima de 4

In [26]:
cities_with_rating_range(df4, 4, 5)

#### col2 - Cidades com média de avaliação abaixo de 2.5

In [27]:
cities_with_rating_range(df4, 0, 2.5)

### Container 3 - Top 10 cidades mais restaurantes com tipos culinários distintos

In [28]:
top_cities_analysis(df4, 'cuisines')

## Cuisines views

### Container 1 - Melhores restaurantes dos principais tipos culinários

In [33]:
best_restaurants_by_cuisine(df4, top_n_cuisines=5)

restaurant_name      cuisines  aggregate_rating  \
422                Brick Store Pub      American               4.9   
1344            Olive Et Gourmando          Cafe               4.9   
366   Andre's Cucina & Polenta Bar       Italian               4.9   
2939               Barbeque Nation  North Indian               4.9   
460                   Antico Pizza         Pizza               4.9   

            city              country_name  
422      Atlanta  United States of America  
1344    Montreal                    Canada  
366     Adelaide                 Australia  
2939  Aurangabad                     India  
460      Atlanta  United States of America

### Container 2 - Top 10 Restaurantes

In [36]:
top_10_restaurants(df4)

restaurant_name              country_name            city  \
811                 The Purple Pig  United States of America         Chicago   
191            Churrascaria Palace                    Brazil  Rio de Janeiro   
4645                        Pabbas                     India       Mangalore   
3766             Indian Grill Room                     India         Gurgaon   
6638                Chin Chin Labs                   England          London   
788   The Cowfish Sushi Burger Bar  United States of America       Charlotte   
814                     Smoque BBQ  United States of America         Chicago   
3498              Kalsang AMA Cafe                     India        Dehradun   
946                     Big Bill's  United States of America          Denver   
6074                    Sushi Masa                 Indonesia         Jakarta   

      aggregate_rating  
811                4.9  
191                4.9  
4645               4.9  
3766               4.9  
6638               4.9  
788                4.9  
814                4.9  
3498               4.9  
946                4.9  
6074               4.9

### Container 3 - Top 10 melhores culinárias

In [39]:
top_10_cuisines_by_rating(df4, top_or_bottom='top')

### Container 4 - Top 10 piores culinárias

In [41]:
top_10_cuisines_by_rating(df4, top_or_bottom='bottom')